In [1]:
import sys
sys.argv.append(["--max-memory", "90%"])

In [2]:
import geopandas as gpd
import os
from src import tessellate_hex
import matplotlib.pyplot as plt
import r5py
import datetime
import pandas as pd
import numpy as np
import time

In [3]:
os.chdir('/Users/benpage/Documents/GitHub/r5food/data')

In [4]:
supermarkets = gpd.read_file('supermarkets.geojson')
tor_boundry = gpd.read_file('tor_boundry.geojson')

In [5]:
boundry_geo = tor_boundry.geometry

In [6]:
supermarkets

id                             address              brand  \
0      48553740                                None           Foodland   
1     241246724      81St. Clair Avenue EastToronto           Farm Boy   
2     254315320                                None              Metro   
3     264107390                                None              Metro   
4     264107691  2490Gerrard Street EastScarborough            FreshCo   
..          ...                                 ...                ...   
228   701945852                                None          No Frills   
229   706078541           McLevin AvenueScarborough          No Frills   
230   797144718          1014Bathurst StreetToronto  Summerhill Market   
231  1042084198                                None            FreshCo   
232  1147510134                                None              Metro   

                           geometry  
0    POINT (633342.871 4837508.068)  
1     POINT (629693.786 4838534.43)  
2    POINT (630876.845 4835192.659)  
3    POINT (637892.508 4838853.286)  
4    POINT (638229.998 4838625.866)  
..                              ...  
228  POINT (642438.992 4846432.813)  
229  POINT (642880.928 4852120.788)  
230   POINT (627871.25 4836539.788)  
231  POINT (633128.789 4847884.513)  
232   POINT (635317.635 4850754.62)  

[233 rows x 4 columns]

In [7]:
def end_time(start_time):
    elapsed_time = time.time() - start_time
    return round(elapsed_time, 2)

In [8]:
def format_travel_times(travel_times, hex_grid, brand, mode):
    travel_times = travel_times.dropna(subset=['travel_time'])
    idx = travel_times.groupby('from_id')['travel_time'].idxmin()
    min_travel_times = travel_times.loc[idx]
    
    clean_df = pd.merge(hex_grid, min_travel_times, left_on='id', right_on='from_id', how = 'left')
    clean_df.drop(labels='from_id', axis=1, inplace = True)
    
    clean_df.rename(columns={'to_id':'store_id'}, inplace = True)
    clean_df['brand'] = brand
    clean_df['transport_mode'] = mode
    
    return clean_df

In [9]:
def calc_travel_times(r5_mode, origins, dests):
    travel_time_matrix = r5py.TravelTimeMatrix(
    transport_network,
    origins=origins,
    destinations=dests,
    transport_modes=[r5_mode],
    departure_time_window=datetime.timedelta(minutes=120),    
    departure=datetime.datetime(2025, 4, 11, 16, 0, 0),
    )

    return travel_time_matrix
    

In [10]:
brand_lst = supermarkets['brand'].unique()
transit_modes = ['walk', 'bike', 'car', 'transit']
res = 8

In [ ]:
print('Generating Hex')
origins, hex_grid = tessellate_hex(boundry_geo, res)
start_time = time.time()
print('Loading network')
transport_network = r5py.TransportNetwork('Toronto.osm.pbf', 
                                          gtfs='ttc_gtfs.zip')
print('FIN:', end_time(start_time), 's')

mode_dict = {'walk':r5py.TransportMode.WALK, 
                'bike':r5py.TransportMode.BICYCLE, 
                'car':r5py.TransportMode.CAR, 
                'transit' : r5py.TransportMode.TRANSIT}

data_dir = os.getcwd()
tt_folder = 'travel_times_res' + str(res)
tt_all_path = os.path.join(data_dir, tt_folder)
os.makedirs(tt_all_path, exist_ok=True)

for brand in brand_lst:
    dests = supermarkets.query("brand == @brand")
    brand_start = time.time()

    brand_path = os.path.join(tt_all_path, brand.replace(' ', '_').lower())
    os.makedirs(brand_path, exist_ok=True)
    
    for mode in transit_modes:
        file_name = (brand + '_' + mode + '.geojson').replace(' ', '_').lower()
        output_path = os.path.join(brand_path, file_name)

        if not os.path.exists(output_path):
            mode_start = time.time()
            print('Computing', brand, mode)
            r5_mode = mode_dict[mode]
    
            travel_times = calc_travel_times(r5_mode, origins, dests)
            
            travel_times = format_travel_times(travel_times, hex_grid, brand, mode)
    
            
            
            travel_times.to_file(output_path, driver="GeoJSON")
            
            print('FIN:', brand, mode, res, end_time(mode_start), 's')
            print('Saved to', output_path)
        else:
            print('SKIP:',brand, mode, res, 'exists at', output_path)
    

    print('Total time', brand, end_time(brand_start), 's')

Generating Hex
Loading network
FIN: 1.7 s
SKIP: Foodland walk 8 exists at /Users/benpage/Documents/GitHub/r5food/data/travel_times_res8/foodland/foodland_walk.geojson
SKIP: Foodland bike 8 exists at /Users/benpage/Documents/GitHub/r5food/data/travel_times_res8/foodland/foodland_bike.geojson
SKIP: Foodland car 8 exists at /Users/benpage/Documents/GitHub/r5food/data/travel_times_res8/foodland/foodland_car.geojson
SKIP: Foodland transit 8 exists at /Users/benpage/Documents/GitHub/r5food/data/travel_times_res8/foodland/foodland_transit.geojson
Total time Foodland 0.0 s
SKIP: Farm Boy walk 8 exists at /Users/benpage/Documents/GitHub/r5food/data/travel_times_res8/farm_boy/farm_boy_walk.geojson
SKIP: Farm Boy bike 8 exists at /Users/benpage/Documents/GitHub/r5food/data/travel_times_res8/farm_boy/farm_boy_bike.geojson
SKIP: Farm Boy car 8 exists at /Users/benpage/Documents/GitHub/r5food/data/travel_times_res8/farm_boy/farm_boy_car.geojson
SKIP: Farm Boy transit 8 exists at /Users/benpage/Docum

In [ ]:
def concat_gdfs(root_dir, file_name):
    gdfs = []
    for dirpath, dirnames, filenames in os.walk(root_dir):
        for filename in filenames:
              if filename.endswith('.geojson'):
                file_path = os.path.join(dirpath, filename)
                try:
                    # Read the geojson file (no layer parameter needed for geojson)
                    gdf = gpd.read_file(file_path)
                    gdfs.append(gdf)
                    print('Read:', file_path)
                except Exception as e:
                    print(f"Error reading {file_path}: {str(e)}")
    

    
    combined_gdf = pd.concat(gdfs, ignore_index=True)
    if file_name is not None:
        combined_gdf.to_file(file_name)
        print('Saved', file_name)
    return combined_gdf

In [ ]:
res_9_root = '/Users/benpage/Documents/GitHub/r5food/data/travel_times_res9'
res_9_file_name = 'all_travel_times_res9.geojson'
res_9 =  concat_gdfs(res_9_root, res_9_file_name)

In [31]:
res_7.query('brand == "Walmart"').query("transport_mode == 'bike'").explore(column = 'travel_time')

In [ ]:
gpd.read_file('/Users/benpage/Documents/GitHub/r5food/data/travel_times/Walmart/walmart_bike.geojson').explore('travel_time')

In [108]:
m = mergeL.explore(column = 'travel_time', scheme = 'natural_breaks')
m = dests.explore(m = m, colour = 'red', style_kwds = {'radius' : 10})
m